### Graficos usando mapas de la ciudad de Milán 

In [111]:
#exportar librerias necesarias
%matplotlib inline
import pandas as pd
import numpy as np
import warnings
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.io as pio
#import ace_tools as tools
from scipy.stats import gaussian_kde
import geopandas as gpd
import folium
from folium.plugins import FastMarkerCluster
from folium.plugins import HeatMap
from branca.colormap import LinearColormap
from scipy.stats import gaussian_kde
import nbformat
import os

In [30]:
warnings.filterwarnings("ignore")

In [31]:
df_calendar = pd.read_csv('data_clean/calendar.csv')
df_list_de = pd.read_csv('data_clean/listings_detailed.csv')
df_list = pd.read_csv('data_clean/listings.csv')
df_neighbour = pd.read_csv('data_clean/neighbourhoods.csv')
df_reviws_de = pd.read_csv('data_clean/reviews_detailed.csv')
df_reviws_su = pd.read_csv('data_clean/reviews_summary.csv')

In [52]:
df_list_de[['has_availability',
 'availability_30',
 'availability_60',
 'availability_90',
 'availability_365']].head()
#df_reviws_de.columns.tolist()

has_availability  availability_30  availability_60  availability_90  \
0                t               23               53               83   
1                t                5                7                9   
2                t                9               39               69   
3                t               28               58               88   
4                t               30               51               78   

   availability_365  
0               358  
1               221  
2               343  
3               363  
4               353

In [4]:
# Extraer latitudes y longitudes
latitudes = df_list_de['latitude'].dropna()
longitudes = df_list_de['longitude'].dropna()

# Calcular densidad con KDE (estimación de densidad de kernel)
xy = np.vstack([longitudes, latitudes])
kde = gaussian_kde(xy, bw_method=0.1)  # Control de banda ancha
density = kde(xy)

# Crear el mapa de calor geográfico usando scatter plot con la densidad de KDE
plt.figure(figsize=(12, 8))
plt.scatter(longitudes, latitudes, c=density, cmap='hot', s=5, alpha=0.6)
plt.colorbar(label='Densidad de Propiedades')
plt.xlabel('Longitud')
plt.ylabel('Latitud')
plt.title('Mapa de Calor Geográfico de la Densidad de Propiedades')

plt.show()

In [9]:
latitudes = df_list_de['latitude'].dropna()
longitudes = df_list_de['longitude'].dropna()

# Calcular densidad con KDE (estimación de densidad de kernel)
xy = np.vstack([latitudes, longitudes])
kde = gaussian_kde(xy, bw_method=0.1)  
density = kde(xy)

# Crear pares de coordenadas con densidad para el mapa de calor
heat_data = [[lat, lon, d] for lat, lon, d in zip(latitudes, longitudes, density)]

# Crear el mapa con centro en la media de las coordenadas
centro_lat = latitudes.mean()
centro_lon = longitudes.mean()
mapa = folium.Map(location=[centro_lat, centro_lon], zoom_start=12)

HeatMap(heat_data, radius=10, blur=15, max_zoom=1).add_to(mapa)

mapa

In [5]:
lats2024 = df_list_de['latitude'].tolist()
lons2024 = df_list_de['longitude'].tolist()
locations = list(zip(lats2024, lons2024))
 
map1 = folium.Map(location=[45.46427, 9.18951], zoom_start=12)
FastMarkerCluster(data=locations).add_to(map1)
 
map1

In [6]:
px.scatter_mapbox(df_list_de, lat='latitude', lon='longitude', size='price', zoom=10, mapbox_style='carto-positron', title='AirBnb - distribución de locales en Milán', template= "plotly_dark", size_max=20, animation_frame='room_type')

In [57]:
zonas_interes = ['DUOMO', 'BRERA', 'TICINESE']
tipo_propiedad = ['Entire serviced apartment', 'Entire rental unit', 'Entire guest suite', 'Entire condo', 'Entire loft']

df_sub = df_list_de[
    (df_list_de['neighbourhood_cleansed'].isin(zonas_interes)) &
    (df_list_de['property_type'].isin(tipo_propiedad))
][['id', 'neighbourhood_cleansed', 'property_type', 'latitude', 'longitude', 'accommodates', 'bedrooms', 'beds']]

# estimar el tamaño de la vivienda m2
df_sub['estimated_size_m2'] = (df_sub['accommodates'] * 10) + (df_sub['bedrooms'] * 12) + (df_sub['beds'] * 4) + np.random.uniform(8, 28, size=len(df_sub))

# Agregar columna de precio por m2
df_sub['price_per_m2'] = 10758

# Calcular el precio estimado
df_sub['estimated_price'] = df_sub['estimated_size_m2'] * df_sub['price_per_m2']

df_sub[['id', 'neighbourhood_cleansed', 'property_type', 'latitude', 'longitude', 'estimated_size_m2', 'price_per_m2', 'estimated_price']].to_csv('./data_clean/df_sub.csv', index=False)

df_sub

id neighbourhood_cleansed       property_type  \
3                   309905               TICINESE  Entire rental unit   
8                   335766               TICINESE  Entire rental unit   
14                  348448                  BRERA  Entire rental unit   
15                  364897               TICINESE  Entire rental unit   
25                  383918               TICINESE         Entire loft   
...                    ...                    ...                 ...   
24303  1182013426759729827               TICINESE  Entire rental unit   
24321  1183056991447816905                  BRERA  Entire rental unit   
24329  1183157975488403483                  DUOMO  Entire rental unit   
24330  1183215972889672263                  BRERA        Entire condo   
24331  1183223791596156389                  DUOMO  Entire rental unit   

        latitude  longitude  accommodates  bedrooms  beds  estimated_size_m2  \
3      45.443830   9.178600             4       2.0   3.0          86.876815   
8      45.452060   9.181010             2       1.0   1.0          57.493345   
14     45.476170   9.188730             2       0.0   1.0          43.603202   
15     45.454610   9.175540             4       1.0   2.0          68.312206   
25     45.449795   9.177659             2       1.0   1.0          54.374124   
...          ...        ...           ...       ...   ...                ...   
24303  45.447183   9.178697             4       1.0   2.0          84.073825   
24321  45.480390   9.183300             2       1.0   1.0          58.908443   
24329  45.456860   9.183190             3       1.0   1.0          61.828910   
24330  45.478966   9.187570             3       1.0   2.0          61.441205   
24331  45.467140   9.182570             4       1.0   2.0          81.037688   

       price_per_m2  estimated_price  
3             10758    934620.773126  
8             10758    618513.402300  
14            10758    469083.251105  
15            10758    734902.708444  
25            10758    584956.827902  
...             ...              ...  
24303         10758    904466.211447  
24321         10758    633737.029553  
24329         10758    665155.415194  
24330         10758    660984.480937  
24331         10758    871803.444152  

[3028 rows x 11 columns]

In [58]:
# Definir constantes de gastos iniciales y anuales
gastos_iniciales = 20000
gastos_anuales = 15000

# Calcular Ingreso Bruto Anual basado en el precio por noche y disponibilidad anual
df_sub['ingreso_bruto_anual'] = (df_list_de['price'] * df_list_de['availability_365']) - gastos_anuales

# Calcular el Costo Total de Inversión
df_sub['costo_total_inversion'] = df_sub['estimated_price'] + gastos_iniciales

# Calcular el Tiempo de Retorno de Inversión en años (ROI)
df_sub['tiempo_retorno'] = df_sub['costo_total_inversion'] / df_sub['ingreso_bruto_anual']

df_sub.to_csv('./data_clean/df_sub.csv', index=False)

In [80]:
#incluimos la columna 'price' al dataser df_sub
df_sub = df_sub.merge(df_list_de[['id', 'price']], on='id', how='left')
df_sub.to_csv('./data_clean/df_sub.csv', index=False)

In [81]:
df_sub.head(16)

id neighbourhood_cleansed       property_type   latitude  longitude  \
0   309905               TICINESE  Entire rental unit  45.443830   9.178600   
1   335766               TICINESE  Entire rental unit  45.452060   9.181010   
2   348448                  BRERA  Entire rental unit  45.476170   9.188730   
3   364897               TICINESE  Entire rental unit  45.454610   9.175540   
4   383918               TICINESE         Entire loft  45.449795   9.177659   
5   392296               TICINESE  Entire rental unit  45.451750   9.180400   
6   141833                  DUOMO  Entire rental unit  45.460240   9.180630   
7   403602                  DUOMO        Entire condo  45.461708   9.188032   
8   412833                  DUOMO        Entire condo  45.461731   9.192669   
9   233795                  BRERA        Entire condo  45.473241   9.186647   
10  234244               TICINESE  Entire rental unit  45.457680   9.177130   
11  423437               TICINESE  Entire rental unit  45.447540   9.177090   
12  426809               TICINESE  Entire rental unit  45.451170   9.180760   
13  431719                  DUOMO  Entire rental unit  45.460700   9.186530   
14  434334                  DUOMO        Entire condo  45.461320   9.184130   
15  451490                  DUOMO  Entire rental unit  45.460040   9.180000   

    accommodates  bedrooms  beds  estimated_size_m2  price_per_m2  \
0              4       2.0   3.0          86.876815         10758   
1              2       1.0   1.0          57.493345         10758   
2              2       0.0   1.0          43.603202         10758   
3              4       1.0   2.0          68.312206         10758   
4              2       1.0   1.0          54.374124         10758   
5              2       1.0   1.0          48.470217         10758   
6              2       1.0   1.0          60.290446         10758   
7              3       1.0   7.0          79.068229         10758   
8              5       2.0   4.0         114.250759         10758   
9              3       2.0   4.0          85.349477         10758   
10             6       3.0   5.0         142.528672         10758   
11             3       2.0   2.0          79.620778         10758   
12             3       1.0   3.0          72.484682         10758   
13             8       3.0   4.0         146.064568         10758   
14             2       1.0   1.0          61.023396         10758   
15             4       1.0   2.0          81.601578         10758   

    estimated_price  ingreso_bruto_anual  costo_total_inversion  \
0      9.346208e+05              57600.0           9.546208e+05   
1      6.185134e+05              17120.0           6.385134e+05   
2      4.690833e+05              16328.0           4.890833e+05   
3      7.349027e+05               1089.0           7.549027e+05   
4      5.849568e+05              49440.0           6.049568e+05   
5      5.214426e+05              -3255.0           5.414426e+05   
6      6.486046e+05              -7050.0           6.686046e+05   
7      8.506160e+05              46250.0           8.706160e+05   
8      1.229110e+06              43220.0           1.249110e+06   
9      9.181897e+05              78349.0           9.381897e+05   
10     1.533323e+06             154587.0           1.553323e+06   
11     8.565603e+05              10056.0           8.765603e+05   
12     7.797902e+05              50340.0           7.997902e+05   
13     1.571363e+06              33930.0           1.591363e+06   
14     6.564897e+05              27175.0           6.764897e+05   
15     8.778698e+05              10100.0           8.978698e+05   

    tiempo_retorno  price  
0        16.573277  200.0  
1        37.296344  220.0  
2        29.953653   89.0  
3       693.207262   93.0  
4        12.236182  180.0  
5      -166.341812  135.0  
6       -94.837535  150.0  
7        18.824130  175.0  
8        28.901195  410.0  
9        11.974495  277.0  
10       10.048215  571.0  
11       87.16

In [71]:
df_sub_12 = df_sub[(df_sub['tiempo_retorno'] >= 4) & (df_sub['tiempo_retorno'] <= 10)]
map2 = folium.Map(location=[45.46427, 9.18951], zoom_start=13)
for coord in df_sub_12.itertuples(index=False):
    folium.Marker(
    location=(coord.latitude, coord.longitude),
    tooltip=f"Inversión: {coord.costo_total_inversion:.2f}€ \n\n Tiempo de Retorno: {coord.tiempo_retorno:.2f} años"
).add_to(mapa).add_to(map2)
map2

In [87]:
px.scatter_mapbox(df_sub, lat='latitude', lon='longitude', size='price', zoom=11, mapbox_style='carto-positron', title='AirBnb - distribución de locales en Milán', template= "plotly_dark", size_max=20, animation_frame='property_type')

In [75]:
#df_list_de['neighbourhood_cleansed'].unique()
#df_list_de['property_type'].unique()
df_sub


id neighbourhood_cleansed       property_type  \
3                   309905               TICINESE  Entire rental unit   
8                   335766               TICINESE  Entire rental unit   
14                  348448                  BRERA  Entire rental unit   
15                  364897               TICINESE  Entire rental unit   
25                  383918               TICINESE         Entire loft   
...                    ...                    ...                 ...   
24303  1182013426759729827               TICINESE  Entire rental unit   
24321  1183056991447816905                  BRERA  Entire rental unit   
24329  1183157975488403483                  DUOMO  Entire rental unit   
24330  1183215972889672263                  BRERA        Entire condo   
24331  1183223791596156389                  DUOMO  Entire rental unit   

        latitude  longitude  accommodates  bedrooms  beds  estimated_size_m2  \
3      45.443830   9.178600             4       2.0   3.0          86.876815   
8      45.452060   9.181010             2       1.0   1.0          57.493345   
14     45.476170   9.188730             2       0.0   1.0          43.603202   
15     45.454610   9.175540             4       1.0   2.0          68.312206   
25     45.449795   9.177659             2       1.0   1.0          54.374124   
...          ...        ...           ...       ...   ...                ...   
24303  45.447183   9.178697             4       1.0   2.0          84.073825   
24321  45.480390   9.183300             2       1.0   1.0          58.908443   
24329  45.456860   9.183190             3       1.0   1.0          61.828910   
24330  45.478966   9.187570             3       1.0   2.0          61.441205   
24331  45.467140   9.182570             4       1.0   2.0          81.037688   

       price_per_m2  estimated_price  ingreso_bruto_anual  \
3             10758    934620.773126              57600.0   
8             10758    618513.402300              17120.0   
14            10758    469083.251105              16328.0   
15            10758    734902.708444               1089.0   
25            10758    584956.827902              49440.0   
...             ...              ...                  ...   
24303         10758    904466.211447               6504.0   
24321         10758    633737.029553              10400.0   
24329         10758    665155.415194             152900.0   
24330         10758    660984.480937               6492.0   
24331         10758    871803.444152              31148.0   

       costo_total_inversion  tiempo_retorno  
3              954620.773126       16.573277  
8              638513.402300       37.296344  
14             489083.251105       29.953653  
15             754902.708444      693.207262  
25             604956.827902       12.236182  
...                      ...             ...  
24303          924466.211447      142.138101  
24321          653737.029553       62.859330  
24329          685155.415194        4.481069  
24330          680984.480937      104.895946  
24331          891803.444152       28.631162  

[3028 rows x 14 columns]

In [126]:
#feq=df_list_de['neighbourhood'].value_counts().sort_index()
feq=df_list_de[df_list_de['neighbourhood']==2]
feq=feq.groupby('neighbourhood')['price'].mean().sort_values(ascending=True)

In [161]:
# Agrupar por 'neighbourhood' y calcular el precio promedio
feq = df_list.groupby('neighbourhood')['price'].mean().reset_index()

# Renombrar la columna de precio
feq.rename(columns={'price': 'avg_price'}, inplace=True)

# Ver los primeros registros de feq
print(feq.head(10))

  neighbourhood   avg_price
0       ADRIANO  136.379310
1        AFFORI  136.020000
2        BAGGIO   88.500000
3    BANDE NERE  130.417749
4        BARONA  100.921875
5       BICOCCA  159.164835
6        BOVISA  132.224576
7     BOVISASCA  123.125000
8         BRERA  255.273547
9      BRUZZANO   71.666667


In [162]:
#df_list_de.columns.tolist()
#df_list_de['neighbourhood']
feq.head()

neighbourhood   avg_price
0       ADRIANO  136.379310
1        AFFORI  136.020000
2        BAGGIO   88.500000
3    BANDE NERE  130.417749
4        BARONA  100.921875

In [165]:
adam = gpd.read_file("data_clean/neighbourhoods.geojson")
feq= feq.transpose()
adam = pd.merge(adam, feq, on='neighbourhood', how='left')
adam.rename(columns= {"price":"avg_price"}, inplace= True)
adam.avg_price = adam.avg_price.round(decimals=2)


In [164]:
# Calcular el promedio de 'price' por 'neighbourhood'
avg_price_per_neighbourhood = df_list.groupby('neighbourhood')['price'].mean().reset_index()

# Cargar el promedio en 'adam' haciendo coincidir los nombres de los barrios
adam = adam.merge(avg_price_per_neighbourhood, on='neighbourhood', how='left')

# Renombrar la columna 'price' en adam a 'avg_price' para mayor claridad
adam.rename(columns={"price": "avg_price"}, inplace=True)

# Redondear 'avg_price' a dos decimales
adam['avg_price'] = adam['avg_price'].round(2)

In [166]:
# Comparar valores únicos entre ambos conjuntos
only_in_adam = neighbourhood_adam - neighbourhood_avg_price
only_in_avg_price = neighbourhood_avg_price - neighbourhood_adam

# Mostrar los barrios que están solo en cada DataFrame
print("Present only in 'adam':", only_in_adam)
print("Present only in 'avg_price_per_neighbourhood':", only_in_avg_price)

Present only in 'adam': set()
Present only in 'avg_price_per_neighbourhood': set()


In [167]:
#df_list.columns.tolist()
#df_list['neighbourhood']
#avg_price_per_neighbourhood
#adam['neighbourhood']
avg_price_per_neighbourhood['neighbourhood']

0          ADRIANO
1           AFFORI
2           BAGGIO
3       BANDE NERE
4           BARONA
          ...     
83     VIALE MONZA
84       VIGENTINA
85    VILLAPIZZONE
86      WASHINGTON
87      XXII MARZO
Name: neighbourhood, Length: 88, dtype: object

In [168]:
#print(adam.columns)
adam

neighbourhood neighbourhood_group  \
0                  SACCO                None   
1               COMASINA                None   
2             STEPHENSON                None   
3                   QT 8                None   
4            ORTOMERCATO                None   
..                   ...                 ...   
83  PARCO BOSCO IN CITT
                None   
84          PORTA ROMANA                None   
85     PARCO DEI NAVIGLI                None   
86                PAGANO                None   
87  GARIBALDI REPUBBLICA                None   

                                             geometry    avg_price  
0   MULTIPOLYGON (((9.12195 45.51602, 9.12163 45.5...        209.8  
1   MULTIPOLYGON (((9.16887 45.52396, 9.16804 45.5...       187.44  
2   MULTIPOLYGON (((9.12932 45.50998, 9.12973 45.5...       106.75  
3   MULTIPOLYGON (((9.14368 45.48474, 9.14338 45.4...   126.340426  
4   MULTIPOLYGON (((9.23739 45.45588, 9.23731 45.4...   119.211538  
..                                                ...          ...  
83  MULTIPOLYGON (((9.09998 45.48789, 9.10146 45.4...        113.0  
84  MULTIPOLYGON (((9.21002 45.44739, 9.21018 45.4...   157.140594  
85  MULTIPOLYGON (((9.15266 45.4152, 9.152 45.4163...  1719.166667  
86  MULTIPOLYGON (((9.16506 45.46684, 9.16486 45.4...   228.052209  
87  MULTIPOLYGON (((9.19872 45.48484, 9.19836 45.4...   202.415512  

[88 rows x 4 columns]

In [172]:
map_dict = adam.set_index('neighbourhood')['avg_price'].to_dict()
color_scale = LinearColormap(["yellow",
 "red"], vmin = min(map_dict.values()), vmax = max(map_dict.values()))
colormap = LinearColormap(
    colors=['green', 'yellow', 'red'],
    vmin=adam['avg_price'].min(),
    vmax=adam['avg_price'].max()
)
 
def get_color(feature):
    value = map_dict.get(feature['properties']['neighbourhood'])
    if value is not None:
        return color_scale(value)
    else:
        return 'grey'
"""def get_color(feature):
    return colormap(feature['properties']['avg_price'])"""


"def get_color(feature):\n    return colormap(feature['properties']['avg_price'])"

In [184]:
adam['formatted_avg_price'] = adam['avg_price'].apply(lambda x: f"€{x:.2f}" if pd.notnull(x) else "Sin datos")


In [185]:
map3 = folium.Map(location=[45.46427, 9.18951], zoom_start=11)
folium.GeoJson(data=adam,
               name='Milan',
              tooltip = folium.features.GeoJsonTooltip(
    fields=['neighbourhood', 'formatted_avg_price'],
    aliases=['Barrio:', 'Precio promedio (€):'],
    labels=True,
    sticky=True,
    style=(
        "background-color: white; color: #333333; font-family: Arial; font-size: 14px; padding: 5px;"
    ),
    sticky_style=(
        "background-color: #F0F0F0; color: #333333; font-family: Arial; font-size: 14px; padding: 5px;"
    )
),

               style_function= lambda feature: {
                   'fillColor': get_color(feature),
                   'color': 'black',
                   'weight': 1,
                   'dashArray': '5, 5',
                   'fillOpacity':0.9
                   },
               highlight_function=lambda feature: {'weight':3, 'fillColor': get_color(feature), 'fillOpacity': 0.8}).add_to(map3)

In [186]:
map3